In [1]:
import os
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from matplotlib.font_manager import FontProperties
from matplotlib.lines import Line2D

# 0 Set the font

In [2]:
COLOR = 'black'
def Load_style():
    try:
        plt.style.use("chartlab.mplstyle")
    except:
        pass
    plt.rcParams['font.sans-serif'] = ['Times New Roman']
    plt.rcParams["axes.unicode_minus"]= False
    # Sets the global font color
    plt.rcParams['text.color'] = COLOR
    plt.rcParams['axes.labelcolor'] = COLOR
    plt.rcParams['xtick.color'] = COLOR
    plt.rcParams['ytick.color'] = COLOR

    # Set the global font bold
    plt.rcParams['font.weight'] = 'bold'
    plt.rcParams['axes.labelweight'] = 'bold'
    font_path = '../data/fonts/Times New Roman.ttf'
    font = FontProperties(fname=font_path, size=14)
    return font

# 1 Drawing method

In [3]:
def small_image(
        axs,
        row, col,
        name,
        data,
        angles,
        data_label,
        radar_labels,
        colors,
        fontsize,

):
    font = Load_style()
    axs[row, col].set_thetagrids(angles * 180 / np.pi, radar_labels, fontproperties=font, fontsize=fontsize-8)
    for index in range(data.shape[1]):
        axs[row, col].plot(angles, data[:, index], 'o-', label=data_label[index], color=colors[index], linewidth=1.5, alpha=0.6)
    # Use the text method to set the title
    axs[row, col].text(-0.25, 1.1, name[:2], transform=axs[row, col].transAxes,
                       fontproperties=font, fontsize=fontsize, ha='left', va='center')
    axs[row, col].text(-0.1, 1.1, name[2:], transform=axs[row, col].transAxes,
                       fontproperties=font, fontsize=fontsize-6, ha='left', va='center')
    axs[row, col].grid(True)


def draw_ldt(
    angles, 
    data, 
    radar_labels, 
    data_label, 
    colors, 
    fontsize=24,
    is_show=False,
    save_path='radar_chart.png'):
    font = Load_style()
    fig = plt.figure(facecolor='white', figsize=(10, 8))
    plt.subplot(111, polar=True)
    plt.thetagrids(angles * 180 / np.pi, radar_labels, fontproperties=font, fontsize=fontsize-6)
    for index in range(data.shape[1]):
        plt.plot(angles, data[:, index], 'o-', label=data_label[index], color=colors[index], linewidth=1.5, alpha=0.6)
    name = os.path.basename(save_path).replace("radar_chart.png", "")
    plt.title(name, loc='left', fontproperties=font, fontsize=fontsize)
    plt.grid(True)
    if is_show: plt.show()  # show
    plt.savefig(save_path, dpi=500)
    plt.close()

# 2 Read the data

In [4]:
df = pd.read_csv('../data/gnn-result.csv')
traitsDict = {}
kernelsDict = {}
kernels = df['kernel'].unique()
for index, row in df.iterrows():
    tz = str(row['traits'])
    if len(tz) != 3:
        if tz == '1': tz = '001'
        if tz == '10': tz = '010'
        if tz == '11': tz = '011'
    traitsDict[tz] = {}
    kernelsDict[row['kernel']] = {}
scoreDictList = {}
for index0, kernel in enumerate(kernels):
    for index, row in df.iterrows():
        if row['kernel'] == kernel:
            tz = str(row['traits'])
            if len(tz) != 3:
                if tz == '1': tz = '001'
                if tz == '10': tz = '010'
                if tz == '11': tz = '011'
            kernelList = [
                row['Top2'],
                row['AUC'],
                row['MCC'],
                row['Jaccard'],
                row['Precision'],
                row['Recall']
            ]
            kernelsDict[kernel][tz] = kernelList
            traitsDict[tz][kernel] = kernelList
data_labels1_ = np.array([
    'Atom-type',
    'Atom-based',
    'Topol-based',
    'Atom-type+Atom-based',
    'Atom-type+Topol-based',
    'Atom-based+Topol-based',
    'Atom-type+Atom-based+Topol-based'
])
data_labels2_ = np.array(['TAG', 'ClusterGCN', 'FiLM', 'SAGE', 'Transformer', 'MF', 'GAT', 'GCN', 'GIN'])
data_labels3_ = np.array([
    'A. TAG',
    'B. ClusterGCN',
    'C. FiLM',
    'D. SAGE',
    'E. Transformer',
    'F. MF'])
dataList = []
n = 6
angles_ = np.linspace(0, 2 * np.pi, n, endpoint=False)
angles_ = np.concatenate((angles_, [angles_[0]]))
radar_labels_ = np.array([
    '', 
    '    AUC', 
    'MCC     ', 
    'Jaccard          ', 
    'Precision          ', 
    '       Recall', 
    '     Top2']
                        )
colors_ = [
    '#52bcec',      # 100
    '#d75425',      # 010
    '#e6b532',      # 001
    '#a21d2f',      # 110
    '#7e2f8c',      # 101
    '#2b2a76',      # 011
    '#73aa43'       # 111
]
saveDir = './'
dataDict = {}
if not os.path.exists(saveDir): os.mkdir(saveDir)
for key, items in kernelsDict.items():
    data1 = []
    for kernel, item in items.items():
        data1.append(item)
    data1 = np.array(data1).T
    data_ = np.concatenate((data1, [data1[0]]))
    dataDict[key] = data_

# 3 Start drawing

In [5]:
len(angles_)

7

In [6]:
len(dataDict[data_labels2_[0]])

7

In [7]:
fig, axs = plt.subplots(nrows=2, ncols=3, subplot_kw=dict(polar=True), facecolor='white', figsize=(16, 10), dpi=600)
i_ = 2
j_ = 3
k_ = 0
custom_lines = []
for l_ in range(len(data_labels1_)):
    custom_lines.append(Line2D([0], [0], marker='o', color=colors_[l_], label=data_labels1_[l_], markerfacecolor=colors_[l_], markersize=15))
for row_ in range(i_):
    for col_ in range(j_):
        small_image(
            axs=axs,
            row=row_, col=col_,
            name=data_labels3_[k_],
            data=dataDict[data_labels2_[k_]],
            angles=angles_,
            colors=colors_,
            data_label=data_labels1_,
            radar_labels=radar_labels_,
            fontsize=24,
        )
        k_ += 1

# Add a general legend
font_ = Load_style()
fig.legend(
    handles=custom_lines,
    loc=8,          # lower
    # bbox_to_anchor=(0.5, 0.),
    ncol=len(data_labels1_)/2,
    prop=font_,
    fontsize=24 - 6)
# Adjust the layout to avoid overlapping
plt.tight_layout()
# Adjust the margins of the subgraph
plt.subplots_adjust(
    # left=0.05,
    # right=0.95,
    bottom=0.15,
    # top=2.1,
    wspace=0.3, hspace=0.3
    )
plt.savefig(os.path.join(saveDir, 'radar_chart.png'))
plt.show()

findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following families were found: Times New Roman
findfont: Generic family 'sans-serif' not found because none of the following fa